# Setup 

In [1]:
import numpy as np 
import pandas as pd 

# file paths 
file_path = f"C://Users//YOUR_FILE_PATH" 

# turn off the setting with copy warning 
pd.options.mode.chained_assignment = None  

# Format GPX File 

In [2]:
import gpxpy 

# load GPX file 
with open(f"{file_path}//Black Hills 50 Course.gpx", "r") as gpx_file: 
    gpx = gpxpy.parse(gpx_file) 

# loop through the points and get the info on each 
data = [] 
for track in gpx.tracks:
    for segment in track.segments:
        for point in segment.points:
            data.append([point.latitude, point.longitude, point.elevation]) 

# create a dataframe from it 
df = pd.DataFrame(data, columns = ["LATITUDE", "LONGITUDE", "ELEVATION"]) 

## Distance Calculation 

In [3]:
from geopy.distance import geodesic 

# get the previous lat/long coordinates 
df["LATITUDE_PREV"] = df["LATITUDE"].shift(1) 
df["LONGITUDE_PREV"] = df["LONGITUDE"].shift(1) 

# create a function to calculate the distance between current and previous points 
def calculate_distance(row):
    try:
        return geodesic(
            (row["LATITUDE_PREV"], row["LONGITUDE_PREV"]), 
            (row["LATITUDE"], row["LONGITUDE"])
        ).miles 
    except:
        return None 

# apply the function to calculate the distance 
df["DISTANCE"] = df.apply(calculate_distance, axis = 1) 

# calculate the cumulative distance 
df["DISTANCE_CUM"] = df["DISTANCE"].cumsum().fillna(0) 

## Elevation Calculations 

In [4]:
# converstion factor for meters to feet 
METERS_TO_FEET = 3.28084 

# convert elevation to feet 
df["ELEVATION"] = df["ELEVATION"] * METERS_TO_FEET 

# calculate the elevation difference between the current and last points 
df["ELEVATION_PREV"] = df["ELEVATION"].shift(1) 
df["ELEVATION_DIFF"] = df["ELEVATION"] - df["ELEVATION_PREV"] 

# Interval Calculations 

In [7]:
# read in the aid station data 
df_intervals = pd.read_csv(f"{file_path}//aid_stations.csv") 

# rename some columns 
df_intervals = df_intervals.rename(columns = {
    "Name": "START_NAME", 
    "Mileage": "START_MILES"
})

# get the next stations for the interval ends 
df_intervals["END_NAME"] = df_intervals.shift(-1) 
df_intervals["END_MILES"] = df_intervals["START_MILES"].shift(-1) 
df_intervals = df_intervals.dropna().reset_index(drop = True) 

# add the interval number 
df_intervals["INTERVAL_NUM"] = df_intervals.index + 1 

## Interval Lookup Function 

In [8]:
# function to lookup the interval number based on the mileage 
def lookup_interval_num(miles):

    # filter the intervals by the current mileage 
    df2 = df_intervals.loc[(df_intervals["START_MILES"] <= miles) & 
                           (df_intervals["END_MILES"] > miles)] 
    
    # return the interval number if an interval is found 
    if len(df2.index) > 0:
        return df2.iloc[0]["INTERVAL_NUM"] 
    else:
        return None 

# apply the function to the dataframe 
df["INTERVAL_NUM"] = df["DISTANCE_CUM"].apply(lookup_interval_num) 

# Creating the Visualizations 

## Overall Elevation Profile 

In [ ]:
import plotly.graph_objects as go 

# function for creating an elevation profile 
def plot_elevation_profile(df, title = ""): 

    # create a new figure 
    fig = go.Figure() 

    # create the tooltip column 
    df["TOOLTIP"] = (
        " - Elevation: " + df["ELEVATION"].apply(lambda x: f"{x:,.0f}") + " ft <br>" + 
        " - Distance: " + df["DISTANCE_CUM"].apply(lambda x: f"{x:,.2f}") + " miles"
    )

    # add the elevation data 
    fig.add_trace(go.Scatter(
        x = df["DISTANCE_CUM"], 
        y = df["ELEVATION"], 
        mode = "lines", 
        line = dict(
            color = "black", 
            width = 2
        ), 
        hoverinfo = "text", 
        text = df["TOOLTIP"]
    ))

    # calculate some metrics about the interval 
    total_gain = df.loc[df["ELEVATION_DIFF"] > 0]["ELEVATION_DIFF"].sum() 
    total_loss = df.loc[df["ELEVATION_DIFF"] < 0]["ELEVATION_DIFF"].sum() 
    total_distance = df["DISTANCE_CUM"].max() - df["DISTANCE_CUM"].min() 

    # put together the annotation text 
    annotation_text = (
        f"Total Gain: {total_gain:,.0f} ft <br>" + 
        f"Total Loss: {abs(total_loss):,.0f} ft <br>" + 
        f"Total Distance: {total_distance:,.0f} miles"
    )

    # add annotation to the top right corner of the plot 
    fig.update_layout(
        annotations = [
            go.layout.Annotation(
                text = annotation_text, 
                xref = "paper", yref = "paper", 
                x = 1, y = 1.2, 
                showarrow = False, 
                font = dict(
                    size = 20, 
                    color = "black"
                )
            )
        ]
    )

    # adjust the figure settings 
    fig.update_layout(
        template = "simple_white", 
        margin = dict(
            l = 100, 
            r = 40, 
            b = 75, 
            t = 80
        ), 
        title = dict(
            text = f"<b>{title}</b>", 
            font = dict(
                size = 28, 
                color = "black", 
                family = "Arial"
            ), 
            x = 0.15, 
            y = 0.95
        ), 
        xaxis = dict(
            title = dict(
                text = "Distance (miles)", 
                font = dict(
                    size = 16
                )
            )
        ), 
        yaxis = dict(
            title = dict(
                text = "Elevation (ft)", 
                font = dict(
                    size = 16
                )
            )
        )
    )

    return fig 

# create and show the overall elevation profile 
fig = plot_elevation_profile(df, title = "Overall Elevation Profile") 
fig.show() 

## Highlight Interval 

In [ ]:
def plot_interval_highlight(df, df_intervals, interval_num): 

    # create the original function 
    fig = plot_elevation_profile(df, title = f"Overall Elevation Profile (interval {interval_num} highlighted)") 

    # get the y range of the plot 
    ymin = fig.data[0]["y"].min() 
    ymax = fig.data[0]["y"].max() 

    # iterate through each interval and add the vertical marker 
    for i, row in df_intervals.iterrows(): 
        xval = row["END_MILES"] 

        # add the vertical marker 
        fig.add_shape(
            type = "line", 
            x0 = xval, x1 = xval, 
            y0 = ymin, y1 = ymax, 
            opacity = 1, 
            line = dict(
                width = 3, 
                dash = "dash", 
                color = "grey"
            )
        )

        # add a rectangle if the interval number matches 
        if row["INTERVAL_NUM"] == interval_num:
            fig.add_shape(
                type = "rect", 
                x0 = row["START_MILES"], 
                x1 = row["END_MILES"], 
                y0 = ymin, y1 = ymax, 
                fillcolor = "grey", 
                opacity = 0.35, 
                line = dict(
                    width = 0
                )
            )

    return fig 

# create and show the overall elevation profile with the interval highlighted 
fig = plot_interval_highlight(df, df_intervals, 3) 
fig.show() 

## Plot Individual Interval 

In [ ]:
def plot_individual_interval(df, interval_num): 

    # filter by the interval number 
    df = df.loc[df["INTERVAL_NUM"] == interval_num] 

    # plot the filtered data 
    fig = plot_elevation_profile(df, title = f"Elevation Profile for Interval {interval_num}") 

    return fig 

# create and show the individual elevation profile 
fig = plot_individual_interval(df, 3) 
fig.show() 